In [1]:
# dataset link (Turkis)
# https://sites.google.com/site/offensevalsharedtask/more-datasets

In [1]:
import os
import numpy as np
import pandas as pd
import pytorch_lightning as pl
import random
import torch
import emoji


import datetime
import numpy as np
import torch.optim as optim


import torch.nn as nn

from torch.utils.data import DataLoader,Dataset,random_split,TensorDataset ,RandomSampler, SequentialSampler
from torchmetrics import Accuracy, F1Score 
from sklearn.preprocessing import LabelEncoder
from pytorch_lightning.callbacks import EarlyStopping,ModelCheckpoint
from pytorch_lightning.loggers import TensorBoardLogger,MLFlowLogger
from sklearn.model_selection import train_test_split

from sklearn.preprocessing import LabelEncoder
from transformers import BertForSequenceClassification, AdamW, BertConfig,BertTokenizer,get_linear_schedule_with_warmup

/home/sebit/anaconda3/envs/dl_env/lib/python3.9/site-packages/neptune/internal/backends/hosted_client.py:51: NeptuneDeprecationWarning: The 'neptune-client' package has been deprecated and will be removed in the future. Install the 'neptune' package instead. For more, see https://docs.neptune.ai/setup/upgrading/
  from neptune.version import version as neptune_client_version
/home/sebit/anaconda3/envs/dl_env/lib/python3.9/site-packages/pytorch_lightning/loggers/neptune.py:39: NeptuneDeprecationWarning: You're importing the Neptune client library via the deprecated `neptune.new` module, which will be removed in a future release. Import directly from `neptune` instead.
  from neptune import new as neptune


In [2]:
device = torch.device("cuda:0" if torch.cuda.is_available() else "cpu")
device

device(type='cuda', index=0)

In [3]:
torch.cuda.is_available()

True

In [4]:
seed_val = 42
random.seed(seed_val)
np.random.seed(seed_val)
torch.manual_seed(seed_val)
torch.cuda.manual_seed_all(seed_val)

# load dataaset


In [5]:
# train_df=pd.read_csv('SemEval-2020 dataset/offenseval2020-turkish/offenseval2020-turkish/offenseval-tr-training-v1/offenseval-tr-training-v1.tsv',sep='\t')
# test_df=pd.read_csv('SemEval-2020 dataset/offenseval2020-turkish/offenseval2020-turkish/offenseval-tr-testset-v1/offenseval-tr-testset-v1.tsv',sep='\t')

In [6]:
train_df=pd.concat([train_df,test_df], axis=0)
train_df=train_df.drop(['id'], axis=1)

NameError: name 'train_df' is not defined

In [ ]:
train_df['subtask_a'].value_counts()

subtask_a
NOT    25231
OFF     6046
Name: count, dtype: int64

In [8]:
data=train_df['tweet'].tolist()
for i in range(len(data)):
    data[i] = data[i].replace('@USER','')
    data[i] = data[i].replace('#','')
    data[i] = data[i].replace('$','')
    data[i] = emoji.demojize(data[i])
    
train_df['tweet'] = data

In [9]:
lab = LabelEncoder()
train_df['subtask_a'] = lab.fit_transform(train_df['subtask_a'])

In [10]:
train_df['subtask_a'].value_counts()

subtask_a
0    25231
1     6046
2     3515
Name: count, dtype: int64

In [11]:
train_df.drop(train_df[train_df['subtask_a'] == 2].index, inplace = True)

In [12]:
train_df['subtask_a'].value_counts()

subtask_a
0    22345
1     5417
Name: count, dtype: int64

In [13]:
train_df

tweet  subtask_a
3515   holstein ineği (alacalı siyah-beyaz inek, yani...          0
3516               Haaaa. O zaman oylar Binali'ye demek.          0
3517    Disk genel merkez yönetimine HDP'nin hiç etki...          0
3518   Bir insanı zorla kaliteli yapamazsın. Sen elin...          0
3519    Sus yaa açtım sonra korkudan telefon elimden ...          0
...                                                  ...        ...
31272  Bu ödül sunan kızı kim giydirdiyse, kızın en b...          0
31273  Bunu sana beddua olarak etmiyorum bunlar ilerd...          0
31274  CHP'liler sandıkları bırakmıyor üstüne oturmuş...          1
31275       karanlığın içinde yalnız kalsam ne oluuuuurr          0
31276   Ne yalan söyleyeyim bu haftalıkta fitil olara...          0

[27762 rows x 2 columns]

In [14]:
data = train_df.tweet.values
labels = train_df.subtask_a.values

# BERT Tokenizer

In [15]:
tokenizer = BertTokenizer.from_pretrained("bert-base-multilingual-cased", do_basic_tokenize=True)
# tokenizer.add_tokens(data)

In [16]:
print(' Original: ', data[78])
print('Tokenized: ', tokenizer.tokenize(data[78]))
print('Token IDs: ', tokenizer.convert_tokens_to_ids(tokenizer.tokenize(data[78])))

 Original:  Sallandık diyorum, merkezi bilmiyorum, sokağa fırlamadım, duruyorum.   Senden bir açıklama gelmeden, ben bu sandığı terketmiyorum 
Tokenized:  ['Sal', '##landı', '##k', 'di', '##yor', '##um', ',', 'merkezi', 'bil', '##mi', '##yor', '##um', ',', 'sok', '##a', '##ğa', 'f', '##ır', '##lama', '##dı', '##m', ',', 'dur', '##uy', '##orum', '.', 'Sen', '##den', 'bir', 'açık', '##lama', 'gel', '##mede', '##n', ',', 'ben', 'bu', 'sand', '##ığı', 'ter', '##ket', '##mi', '##yor', '##um']
Token IDs:  [64831, 35783, 10174, 10120, 26101, 10465, 117, 47522, 13897, 10500, 26101, 10465, 117, 29509, 10113, 25163, 174, 17145, 24540, 17532, 10147, 117, 28959, 53452, 28048, 119, 18082, 10633, 10561, 71769, 24540, 74458, 59268, 10115, 117, 11015, 11499, 45989, 28581, 12718, 13650, 10500, 26101, 10465]


# Tokenize Dataset

In [17]:
max_len = 0
for sent in data:

    input_ids = tokenizer.encode(sent, add_special_tokens=True)
    max_len = max(max_len, len(input_ids))

print('Max sentence length: ', max_len)

Token indices sequence length is longer than the specified maximum sequence length for this model (1277 > 512). Running this sequence through the model will result in indexing errors


Max sentence length:  6906


In [18]:
input_ids = []
attention_masks = []

for sent in data:
    encoded_dict = tokenizer.encode_plus(
                        sent,                     
                        add_special_tokens = True, 
                        max_length = 64,           
                        pad_to_max_length = True,
                        return_attention_mask = True,  
                        return_tensors = 'pt',   
                   )
    
  
    input_ids.append(encoded_dict['input_ids'])
    attention_masks.append(encoded_dict['attention_mask'])


input_ids = torch.cat(input_ids, dim=0)
attention_masks = torch.cat(attention_masks, dim=0)
labels = torch.tensor(labels)


print('Original: ', data[0])
print('Token IDs:', input_ids[0])

Truncation was not explicitly activated but `max_length` is provided a specific value, please use `truncation=True` to explicitly truncate examples to max length. Defaulting to 'longest_first' truncation strategy. If you encode pairs of sequences (GLUE-style) with the tokenizer you can select this strategy more precisely by providing a specific strategy to `truncation`.
/home/sebit/anaconda3/envs/testenv/lib/python3.9/site-packages/transformers/tokenization_utils_base.py:2418: FutureWarning: The `pad_to_max_length` argument is deprecated and will be removed in a future version, use `padding=True` or `padding='longest'` to pad to the longest sequence in the batch, or use `padding='max_length'` to pad to a max length. In this case, you can give a specific length with `max_length` (e.g. `max_length=45`) or leave max_length to None to pad to the maximal input size of the model (e.g. 512 for Bert).
  warnings.warn(


Original:  holstein ineği (alacalı siyah-beyaz inek, yani hollanda ineği) en verimli süt alınan inek ırkıymış, trt belgesel'de öyle söylediler
Token IDs: tensor([   101, 110516,  16206,  10106,  10112,  16054,    113,  21739,  15794,
         10713,  34543,  10237,    118, 110744,  10106,  10707,    117,  84251,
         46232,  41971,  10106,  10112,  16054,    114,  10110,  55011,  98373,
           187,  41559,  10164,  65890,  10106,  10707,    321,  16299,  10713,
         16889,  19733,    117,  32221,  10123,  34831,  12912,    112,  10104,
           276,  18369, 100721,  18369,  28113,  10165,    102,      0,      0,
             0,      0,      0,      0,      0,      0,      0,      0,      0,
             0])


# Split Dataset

In [19]:
dataset = TensorDataset(input_ids, attention_masks, labels)
train_size = int(0.9 * len(dataset))
val_size = len(dataset) - train_size


train_dataset, val_dataset = random_split(dataset, [train_size, val_size])

print('{:>5,} training samples'.format(train_size))
print('{:>5,} validation samples'.format(val_size))

24,985 training samples
2,777 validation samples


In [20]:
from transformers import BertForSequenceClassification, AdamW, BertConfig

model = BertForSequenceClassification.from_pretrained(
    "bert-base-multilingual-cased",
    num_labels = 2,             
    output_attentions = False,
    output_hidden_states = False, 
)

model.cuda()

Some weights of BertForSequenceClassification were not initialized from the model checkpoint at bert-base-multilingual-cased and are newly initialized: ['classifier.bias', 'classifier.weight']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.


BertForSequenceClassification(
  (bert): BertModel(
    (embeddings): BertEmbeddings(
      (word_embeddings): Embedding(119547, 768, padding_idx=0)
      (position_embeddings): Embedding(512, 768)
      (token_type_embeddings): Embedding(2, 768)
      (LayerNorm): LayerNorm((768,), eps=1e-12, elementwise_affine=True)
      (dropout): Dropout(p=0.1, inplace=False)
    )
    (encoder): BertEncoder(
      (layer): ModuleList(
        (0-11): 12 x BertLayer(
          (attention): BertAttention(
            (self): BertSelfAttention(
              (query): Linear(in_features=768, out_features=768, bias=True)
              (key): Linear(in_features=768, out_features=768, bias=True)
              (value): Linear(in_features=768, out_features=768, bias=True)
              (dropout): Dropout(p=0.1, inplace=False)
            )
            (output): BertSelfOutput(
              (dense): Linear(in_features=768, out_features=768, bias=True)
              (LayerNorm): LayerNorm((768,), eps=1e-12

In [21]:
params = list(model.named_parameters())

print('The BERT model has {:} different named parameters.\n'.format(len(params)))

print('==== Embedding Layer ====\n')

for p in params[0:5]:
    print("{:<55} {:>12}".format(p[0], str(tuple(p[1].size()))))

print('\n==== First Transformer ====\n')

for p in params[5:21]:
    print("{:<55} {:>12}".format(p[0], str(tuple(p[1].size()))))

print('\n==== Output Layer ====\n')

for p in params[-4:]:
    print("{:<55} {:>12}".format(p[0], str(tuple(p[1].size()))))

The BERT model has 201 different named parameters.

==== Embedding Layer ====

bert.embeddings.word_embeddings.weight                  (119547, 768)
bert.embeddings.position_embeddings.weight                (512, 768)
bert.embeddings.token_type_embeddings.weight                (2, 768)
bert.embeddings.LayerNorm.weight                              (768,)
bert.embeddings.LayerNorm.bias                                (768,)

==== First Transformer ====

bert.encoder.layer.0.attention.self.query.weight          (768, 768)
bert.encoder.layer.0.attention.self.query.bias                (768,)
bert.encoder.layer.0.attention.self.key.weight            (768, 768)
bert.encoder.layer.0.attention.self.key.bias                  (768,)
bert.encoder.layer.0.attention.self.value.weight          (768, 768)
bert.encoder.layer.0.attention.self.value.bias                (768,)
bert.encoder.layer.0.attention.output.dense.weight        (768, 768)
bert.encoder.layer.0.attention.output.dense.bias              

In [22]:
optimizer = AdamW(model.parameters(),
                  lr = 2e-5,
                  eps = 1e-8
                )

/home/sebit/anaconda3/envs/testenv/lib/python3.9/site-packages/transformers/optimization.py:411: FutureWarning: This implementation of AdamW is deprecated and will be removed in a future version. Use the PyTorch implementation torch.optim.AdamW instead, or set `no_deprecation_warning=True` to disable this warning
  warnings.warn(


In [23]:
def flat_accuracy(preds, labels):
    pred_flat = np.argmax(preds, axis=1).flatten()
    labels_flat = labels.flatten()
    return np.sum(pred_flat == labels_flat) / len(labels_flat)

In [24]:
def format_time(elapsed):

    elapsed_rounded = int(round((elapsed)))
    return str(datetime.timedelta(seconds=elapsed_rounded))


In [25]:
class sinKafModel(pl.LightningModule):
    def __init__(self, model, optimizer, scheduler):
        super().__init__()
        self.model = model
        self.optimizer = optimizer
        self.scheduler = scheduler


    def forward(self, input_ids, attention_mask, labels):
        outputs = self.model(input_ids, attention_mask=attention_mask, labels=labels)
        return outputs

    def training_step(self, batch, batch_idx):
        input_ids, input_mask, labels = batch
        outputs = self(input_ids, input_mask, labels)
        loss = outputs.loss
        self.log('train_loss', loss)
        return loss

    def validation_step(self, batch, batch_idx):
        input_ids, input_mask, labels = batch
        outputs = self(input_ids, input_mask, labels)
        loss = outputs.loss
        logits = outputs.logits
        preds = torch.argmax(logits, dim=1)
        acc = (preds == labels).sum().item() / len(labels)
        self.log('val_loss', loss)
        self.log('val_acc', acc)
        return loss

    def configure_optimizers(self):
        return [self.optimizer], [self.scheduler]

    # def train_dataloader(self):
    #     return self.train_dataloader

    # def val_dataloader(self):
    #     return self.validation_dataloader


In [26]:
train_dataloader = DataLoader(train_dataset,  sampler = RandomSampler(train_dataset), batch_size = 2 )
validation_dataloader = DataLoader(val_dataset, sampler = SequentialSampler(val_dataset), batch_size = 2 )

In [27]:
epochs = 4
total_steps = len(train_dataloader) * epochs
scheduler = get_linear_schedule_with_warmup(optimizer, 
                                            num_warmup_steps = 0, 
                                            num_training_steps = total_steps)

In [28]:
model = sinKafModel(model, optimizer, scheduler)
trainer = pl.Trainer( max_epochs=epochs, limit_train_batches=0.1, devices=1, accelerator='gpu') 
trainer.fit(model,train_dataloader,validation_dataloader )

GPU available: True (cuda), used: True
TPU available: False, using: 0 TPU cores
IPU available: False, using: 0 IPUs
HPU available: False, using: 0 HPUs
/home/sebit/anaconda3/envs/testenv/lib/python3.9/site-packages/pytorch_lightning/trainer/connectors/logger_connector/logger_connector.py:67: UserWarning: Starting from v1.9.0, `tensorboardX` has been removed as a dependency of the `pytorch_lightning` package, due to potential conflicts with other packages in the ML ecosystem. For this reason, `logger=True` will use `CSVLogger` as the default logger, unless the `tensorboard` or `tensorboardX` packages are found. Please `pip install lightning[extra]` or one of them to enable TensorBoard support by default
  warning_cache.warn(


LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]

  | Name  | Type                          | Params
--------------------------------------------------------
0 | model | BertForSequenceClassification | 177 M 
--------------------------------------------------------
177 M     Trainable params
0         Non-trainable params
177 M     Total params
711.420   Total estimated model params size (MB)


Sanity Checking DataLoader 0:   0%|          | 0/2 [00:00<?, ?it/s]

/home/sebit/anaconda3/envs/testenv/lib/python3.9/site-packages/pytorch_lightning/trainer/connectors/data_connector.py:442: PossibleUserWarning: The dataloader, val_dataloader, does not have many workers which may be a bottleneck. Consider increasing the value of the `num_workers` argument` (try 8 which is the number of cpus on this machine) in the `DataLoader` init to improve performance.
  rank_zero_warn(


/home/sebit/anaconda3/envs/testenv/lib/python3.9/site-packages/pytorch_lightning/trainer/connectors/data_connector.py:442: PossibleUserWarning: The dataloader, train_dataloader, does not have many workers which may be a bottleneck. Consider increasing the value of the `num_workers` argument` (try 8 which is the number of cpus on this machine) in the `DataLoader` init to improve performance.
  rank_zero_warn(


Epoch 0:   0%|          | 1/1249 [00:00<05:01,  4.13it/s, v_num=6]

OutOfMemoryError: CUDA out of memory. Tried to allocate 352.00 MiB (GPU 0; 4.00 GiB total capacity; 2.67 GiB already allocated; 0 bytes free; 2.80 GiB reserved in total by PyTorch) If reserved memory is >> allocated memory try setting max_split_size_mb to avoid fragmentation.  See documentation for Memory Management and PYTORCH_CUDA_ALLOC_CONF

In [ ]:
sent = 'Koyunlar hasta'

In [ ]:
input_ids = []
attention_masks = []

encoded_dict = tokenizer.encode_plus(
                    sent,
                    add_special_tokens = True,
                    max_length = 64,
                    pad_to_max_length = True,
                    return_attention_mask = True,
                    return_tensors = 'pt',
                )


input_ids = encoded_dict['input_ids']
attention_masks = encoded_dict['attention_mask']


input_ids = torch.cat([input_ids], dim=0)
input_mask = torch.cat([attention_masks], dim=0)
labels = torch.tensor(labels)




print('Original: ', sent)
print('Token IDs:', input_ids)
print('Token IDs:', input_mask)

In [ ]:
outputs = model(input_ids, input_mask, labels[0])

In [ ]:
outputs[0]